## Preliminary items

References: 
https://github.com/peanutshawny/lstm-stock-predictor

In [21]:
import re
import string
import unicodedata

# importing
import numpy as np
import pandas as pd
import requests
import spacy
import nltk
nltk.download('stopwords')
nltk.download('vader_lexicon')

nlp = spacy.load('en_core_web_sm')
from nltk.sentiment.vader import SentimentIntensityAnalyzer
from nltk.corpus import stopwords

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package vader_lexicon to /root/nltk_data...
[nltk_data]   Package vader_lexicon is already up-to-date!


In [22]:
pd.set_option('max_colwidth', 400)

In [23]:
%load_ext google.colab.data_table

The google.colab.data_table extension is already loaded. To reload it, use:
  %reload_ext google.colab.data_table


## Mount Google Drive 

In [24]:
currentWorkingDir = !pwd
defaultWorkingDir = "/content"

if ( currentWorkingDir[0] == defaultWorkingDir ):
  from google.colab import drive

  drive.mount('/content/drive')
      
  %cd "/content/drive/My Drive/Colab Notebooks/stock_portfolio"
else:
  print("Currenting running app from: ")
  !pwd

Currenting running app from: 
/content/drive/My Drive/Colab Notebooks/stock_portfolio


# Import articles to dataframe

In [ ]:
df = pd.read_csv("articles.csv")

In [ ]:
df.content = df.content.astype('str')

In [ ]:
df.dtypes

postid             object
post_date          object
instrument_code    object
title              object
link               object
content            object
content_length      int64
dtype: object

In [ ]:
df.head(10)

postid  ... content_length
0  post-1104646  ...             86
1  post-1101933  ...             37
2  post-1096087  ...             29
3  post-1094046  ...             96
4  post-1090194  ...             43
5  post-1085967  ...            121
6  post-1085350  ...             24
7  post-1085327  ...            254
8  post-1085270  ...            123
9  post-1084747  ...             38

[10 rows x 7 columns]

# Clean up data

## Remove articles outside of scope

In [ ]:
df_sentiment = df

In [ ]:
df_sentiment.post_date.min()

'2014-04-11 00:00:00'

In [ ]:
df_sentiment.post_date.max()

'2021-01-21 17:24:00'

In [ ]:
df_sentiment.post_date = pd.to_datetime(df_sentiment.post_date, format="%Y-%m-%d").dt.date
df_sentiment.post_date = pd.to_datetime(df_sentiment.post_date)

In [ ]:
from datetime import datetime
df_sentiment = df_sentiment [(df_sentiment.post_date >= datetime(2016,1,1)) & (df_sentiment.post_date < datetime(2021,1,1)) ]

In [ ]:
df_sentiment.shape

(7400, 7)

In [ ]:
df_sentiment.post_date

0      2020-12-31
1      2020-11-13
2      2020-08-14
3      2020-07-16
4      2020-05-18
          ...    
7776   2016-07-29
7777   2016-05-12
7778   2016-05-12
7779   2016-05-12
7780   2016-03-31
Name: post_date, Length: 7400, dtype: datetime64[ns]

## Remove fields that have no content

In [ ]:
df_sentiment = df_sentiment[df_sentiment.content_length > 0]

## Clean up content field (remove "click here")

Filter for keywords

In [ ]:
df_sentiment[df_sentiment.content.str.contains("|".join(["click here"]),case=False) ]

postid  ... content_length
46    post-945093  ...             27
51    post-943454  ...             18
52    post-941975  ...             27
54    post-938519  ...             27
57    post-356439  ...             27
...           ...  ...            ...
7176  post-351488  ...             66
7316  post-352686  ...             27
7503  post-355346  ...             29
7571  post-332400  ...             27
7678  post-951154  ...             53

[93 rows x 7 columns]

Use regex to remove phrases

In [ ]:
import re

p = re.compile("(Click here to open \\bdocuments?)|(Click here to (download|open))|(Click here to view \\bdocuments?)|(Click here)|(Please click here to download)",re.IGNORECASE)

In [ ]:
df_sentiment["content_clean"] = df_sentiment.content.str.replace(p,"",regex=True)

In [ ]:
df_sentiment[df_sentiment.content.str.contains("|".join(["click here"]),case=False) ]

postid  post_date  ... content_length                    content_clean
46    post-945093 2017-02-09  ...             27                                 
51    post-943454 2016-12-29  ...             18                                 
52    post-941975 2016-11-14  ...             27                                 
54    post-938519 2016-08-12  ...             27                                 
57    post-356439 2016-02-12  ...             27                                 
...           ...        ...  ...            ...                              ...
7176  post-351488 2016-02-04  ...             66                 the financials 2
7316  post-352686 2016-02-05  ...             27                                 
7503  post-355346 2016-02-12  ...             29                                 
7571  post-332400 2016-01-12  ...             27                                 
7678  post-951154 2017-07-04  ...             53   Offer opens on July 19th, 2017

[93 rows x 8 columns]

Get content_clean length

In [ ]:
df_sentiment['content_clean_length'] = df_sentiment.content_clean.str.len()

In [ ]:
filter_click_here = df_sentiment.content.str.contains("|".join(["click here"]),case=False) 

In [ ]:
df_sentiment[filter_click_here]

postid  ... content_clean_length
46    post-945093  ...                    0
51    post-943454  ...                    0
52    post-941975  ...                    0
54    post-938519  ...                    0
57    post-356439  ...                    0
...           ...  ...                  ...
7176  post-351488  ...                   17
7316  post-352686  ...                    0
7503  post-355346  ...                    2
7571  post-332400  ...                    0
7678  post-951154  ...                   31

[93 rows x 9 columns]

Replace fields that contain "click here" with text from URL

In [ ]:
df_sentiment['new_content'] = np.where(filter_click_here, df_sentiment.link,df_sentiment.content_clean)

In [ ]:
d = df_sentiment.link.str.replace("https://www.jamstockex.com/", "")

In [ ]:
e = d.str.replace("-"," ")

In [ ]:
link_txt = e.str.replace("/","")

In [ ]:
df_sentiment['content'] = np.where(filter_click_here,link_txt ,df_sentiment.content_clean)

In [ ]:
df_sentiment['content_length'] = df_sentiment.content.str.len()

In [ ]:
df_sentiment[ df_sentiment.content_length <= 7]

postid  post_date  ... content_clean_length new_content
2351  post-1102287 2020-11-18  ...                    2         \n 
3202   post-482184 2016-05-11  ...                    2         \n 

[2 rows x 10 columns]

Remove the fields with blank values

In [ ]:
column_list = ["postid","post_date","instrument_code","title","link","content"] 
filter_content_len = ~(df_sentiment.content_length <= 7)

df_sentiment = df_sentiment.loc[ filter_content_len, column_list ]

In [ ]:
df_sentiment

Output hidden; open in https://colab.research.google.com to view.

# Create fields based on nature of article

## Create field for articles that pertain to financial reports

In [ ]:
df_sentiment[df_sentiment.content.str.contains("|".join(["quarter","q\d","qtr","audited","report","results","statements","supplementary"]),case=False)]

postid  ...                                                                                 content
0     post-1104646  ...  138 Student Living Jamaica 2020 – Final 138SL Quarterly Report as at 30 September 2020
1     post-1101933  ...                                                   138 SL FS Sept qtr – 2020 – Final Qtr
2     post-1096087  ...                                                           138SL Q3 Financials June 2020
4     post-1090194  ...                                             138SL FS March Qtr 2 2020 138SL Note to JSE
6     post-1085350  ...                                                                138SL Annual Report 2019
...            ...  ...                                                                                     ...
7772   post-941661  ...                              tTech Unaudited Financial Statements at September 30, 2016
7774   post-938792  ...                                                        tTech Limited Annual Report 2015
7775   post-938377  ...                           tTech Limited Unaudited Financial Statements at June 30, 2016
7778   post-486495  ...                                                 tTech 2015 Audited Financial Statements
7779   post-486498  ...                                   tTech Unaudited Financial Statements at March 31 2016

[2031 rows x 6 columns]

In [ ]:
filter_report = df_sentiment.content.str.contains("|".join(["quarter","q\d","qtr","audited","report","results","statements","supplementary"]),case=False)

In [ ]:
df_sentiment['is_regarding_financial_report'] = np.where(filter_report,1,0)

In [ ]:
df_sentiment

Output hidden; open in https://colab.research.google.com to view.

## Create field based on when shares are bought/sold by connected parties

In [ ]:
filter_shares = df_sentiment.content.str.contains("|".join(["sold|purchased"]),case=False) &  df_sentiment.content.str.contains("|".join(["shares"]),case=False)

In [ ]:
df_sentiment[df_sentiment.content.str.contains("|".join(["sold|purchased"]),case=False) &  df_sentiment.content.str.contains("|".join(["shares"]),case=False)]

postid  ... is_regarding_financial_report
5     post-1085967  ...                             0
8     post-1085270  ...                             0
27     post-988855  ...                             0
48     post-944261  ...                             0
49     post-944232  ...                             0
...            ...  ...                           ...
7755   post-954802  ...                             0
7761   post-951349  ...                             0
7768   post-946450  ...                             0
7771   post-942336  ...                             0
7780   post-415008  ...                             0

[2000 rows x 7 columns]

In [ ]:
df_sentiment['is_sold_pur_shares'] = np.where(filter_shares,1,0)

In [ ]:
df_sentiment

Output hidden; open in https://colab.research.google.com to view.

# Function to perform sentiment analysis

In [ ]:
def getSentiment(article):
    """
    function that generates a soup to process text and output sentiment scores
    """

    # empty list for sentiment data
    sentiment_list = np.empty(shape=0, dtype=object)

    # cleaning text by removing punctuation and stopwords, as well as lemmatization
    punctuations = string.punctuation
    sw = stopwords.words('english')

    # converting to unicode
    section = unicodedata.normalize('NFKD', article)
    section = section.replace('\t', ' ').replace('\n', '').replace('/s', '').replace('\'', '')

    # joining, removing unecessary characters, and truncating text
    text = ''.join(section)
    text = re.sub('\s+', ' ', text).strip()
    text = text[:40000]

    # creating spacy nlp variable to tokenize and remove punctuation
    doc = nlp(text)

    doc = [token.lemma_.lower().strip() for token in doc]
    doc = [token for token in doc if token.isalpha()]
    doc = [token for token in doc if token not in punctuations and token not in sw]

    # joining text and getting sentiment
    doc = ' '.join(doc)

    analyzer = SentimentIntensityAnalyzer()
    sentiment = analyzer.polarity_scores(doc)

    sentiment_list = np.append(sentiment_list, sentiment)

    # transposing each type of sentiment (pos, neg, neu) into separate features
    sentiment_df = pd.DataFrame({'sentiment': sentiment_list})

    return sentiment_df

# Add column with article sentiment

In [ ]:
a = df_sentiment['content'].to_list()

In [ ]:
sentimentsList = [getSentiment(x).values[0][0]['compound'] for x in a]

In [ ]:
df_sentiment['sentiment'] = sentimentsList

In [ ]:
df_sentiment

Output hidden; open in https://colab.research.google.com to view.

# Group sentiment information based on date and instrument_code

In [ ]:
df_sentiment_ml = df_sentiment.groupby(["instrument_code","post_date"]).agg({"sentiment":"mean",
                                                                             "is_regarding_financial_report":"min",
                                                                             "is_sold_pur_shares":"min"})

In [ ]:
df_sentiment_ml

sentiment  ...  is_sold_pur_shares
instrument_code post_date              ...                    
138SL           2016-01-05     0.4588  ...                   1
                2016-01-22     0.3182  ...                   0
                2016-02-12    -0.2263  ...                   0
                2016-05-11     0.0000  ...                   0
                2016-06-13     0.2960  ...                   0
...                               ...  ...                 ...
XFUND           2020-07-22    -0.2263  ...                   0
                2020-08-17    -0.2500  ...                   0
                2020-09-16     0.4588  ...                   1
                2020-09-22     0.4588  ...                   1
                2020-10-01     0.4588  ...                   1

[6527 rows x 3 columns]

# Save to CSV

In [35]:
df_sentiment.to_csv("articles_sentiment_processed.csv")
df_sentiment_ml.to_csv("articles_sentiment_processed_ML.csv")

NameError: ignored

# Combine sentiments with prices dataset

## Import into dataframes

In [10]:
sen_df = pd.read_csv("articles_sentiment_processed_ML.csv")
prices_df = pd.read_csv("jse_main_price_2016-2020.csv")

prices_df = prices_df[["Symbol","Date","Close_Price","Today_High","Today_Low","Volume_non_block"]]

In [11]:
sen_df

instrument_code  ... is_sold_pur_shares
0              138SL  ...                  1
1              138SL  ...                  0
2              138SL  ...                  0
3              138SL  ...                  0
4              138SL  ...                  0
...              ...  ...                ...
6522           XFUND  ...                  0
6523           XFUND  ...                  0
6524           XFUND  ...                  1
6525           XFUND  ...                  1
6526           XFUND  ...                  1

[6527 rows x 5 columns]

In [12]:
prices_df

Symbol        Date  ...  Today_Low  Volume_non_block
0               AFS  2016-01-04  ...      16.00            8510.0
1               BRG  2016-01-04  ...       3.15           85100.0
2               CCC  2016-01-04  ...      20.00           10000.0
3               CAR  2016-01-04  ...      60.00         2261300.0
4                GK  2016-01-04  ...      84.00            2483.0
...             ...         ...  ...        ...               ...
63878  FIRSTROCKJMD  2020-12-31  ...      12.48           45211.0
63879     CABROKERS  2020-12-31  ...       1.75            1300.0
63880           TJH  2020-12-31  ...       1.30        10197113.0
63881        LUMBER  2020-12-31  ...       1.45          224630.0
63882      TROPICAL  2020-12-31  ...       1.13          306400.0

[63883 rows x 6 columns]

## Data Preparation: Prices dataframe

###Convert dates from string to datetime to facilite date calculations

In [13]:
prices_df.Date   = pd.to_datetime(prices_df.Date,   format="%Y-%m-%d").dt.date
sen_df.post_date = pd.to_datetime(sen_df.post_date, format="%Y-%m-%d").dt.date

### Field: Previous business day

In [14]:
import datetime
from pandas.tseries.offsets import BDay
# BDay is business day

prices_df["Previous_business_day"] = prices_df.Date.apply(lambda x:(x-pd.tseries.offsets.BDay(1)))
prices_df.Previous_business_day = pd.to_datetime(prices_df.Previous_business_day, format="%Y-%m-%d").dt.date

In [15]:
prices_df

Symbol        Date  ...  Volume_non_block  Previous_business_day
0               AFS  2016-01-04  ...            8510.0             2016-01-01
1               BRG  2016-01-04  ...           85100.0             2016-01-01
2               CCC  2016-01-04  ...           10000.0             2016-01-01
3               CAR  2016-01-04  ...         2261300.0             2016-01-01
4                GK  2016-01-04  ...            2483.0             2016-01-01
...             ...         ...  ...               ...                    ...
63878  FIRSTROCKJMD  2020-12-31  ...           45211.0             2020-12-30
63879     CABROKERS  2020-12-31  ...            1300.0             2020-12-30
63880           TJH  2020-12-31  ...        10197113.0             2020-12-30
63881        LUMBER  2020-12-31  ...          224630.0             2020-12-30
63882      TROPICAL  2020-12-31  ...          306400.0             2020-12-30

[63883 rows x 7 columns]

## Data Preparation: Prices dataframe (per Symbol)

In [17]:
### Function: Used for field "stock_not_traded_date_list"
# Function creates an array of dates that the stock was not traded on

date_lookback_limit = 5 # Determines max dates to lookup
def getDatesToSumSentiments (x):
  
  lb = min(date_lookback_limit, x['no_days_not_traded_since_last_traded'] )
  date_list = list()
  for i in range(1,lb+1):
    date_list.append(
      x['Date'] - pd.tseries.offsets.BDay(i)
    )
  return date_list

In [19]:
# Single df with all data
df_list = list()

for s in prices_df.Symbol.unique():
	
  #### Create prices df for each symbol and sort by Date field
  p_df = prices_df[prices_df.Symbol == s]
  p_df = p_df.sort_values(by='Date', ascending=True)

  #### Create sentiment df for each symbol and sort by Date field 
  s_df = sen_df[sen_df.instrument_code == s]
  s_df = s_df.sort_values(by='post_date', ascending=True)	

  ### Field: Determine if traded on previous business day 
  p_df["is_traded_on_Previous_business_day"] = \
    (p_df.Date.shift() == p_df.Previous_business_day )
    
    
  ### Field: Calculate the previous day last traded
  temp 		 				            = p_df.Date.shift()
  temp.iloc[0] 			        	= p_df.Date[p_df.Date.first_valid_index()]
  p_df["Previous_trade_day"]  = temp


  ### Calculate the number of days that the stock did not trade for prior 
  ### to the current date

  # Function to determine no of business days between dates inclusive
  f = lambda x: (len(pd.bdate_range(x['Previous_trade_day'], x['Date'] )))

  p_df['no_days_not_traded_since_last_traded'] = (p_df.apply(f, axis=1))

  p_df['no_days_not_traded_since_last_traded'] =  \
    p_df['no_days_not_traded_since_last_traded'] - 2 # All values were off by 2 days

  # Set the first date as zero as there is no data for it to check against
  p_df.no_days_not_traded_since_last_traded.iloc[0] = 0 


  ## Field: Determine the dates that the stock did not trade for
  p_df['stock_not_traded_date_list'] = p_df.apply(getDatesToSumSentiments, axis=1)

  ### Convert prices dataframe to 1NF by creating a separate row for each value in
  ### 'stock_not_traded_date_list' field

  p_df = p_df.explode('stock_not_traded_date_list')
    
  ### Convert date fields to string to faciliate join
  p_df.stock_not_traded_date_list = p_df.stock_not_traded_date_list.astype(str)
  p_df.Date = p_df.Date.astype(str)
  s_df.post_date = s_df.post_date.astype(str)

  ### Perform join
  c_df = pd.merge(p_df, s_df, how='left', left_on="stock_not_traded_date_list",right_on="post_date")
  c_df = pd.merge(c_df, s_df, how='left', left_on="Date",right_on="post_date")


  # Group columns
  c_df = c_df.groupby(["Symbol","Date"]).agg({'Close_Price'     :'mean',
                                              'Volume_non_block':'mean',
                                              'no_days_not_traded_since_last_traded':'mean',
                                              'Today_High'      :'mean',
                                              'Today_Low'       :'mean',
                                              'sentiment_x'     :'mean',
                                              'is_regarding_financial_report_x' :'max',
                                              'is_sold_pur_shares_x'            :'max',
                                              'sentiment_y'     :'mean',
                                              'is_regarding_financial_report_y' :'max',
                                              'is_sold_pur_shares_y'            :'max'
                                              })
  
  c_df['sentiment'] =  c_df[["sentiment_x","sentiment_y"]].mean(axis=1)
  c_df['is_regarding_financial_report'] = c_df[["is_regarding_financial_report_x", "is_regarding_financial_report_y"]].max(axis=1)
  c_df['is_sold_pur_shares'] = c_df[["is_sold_pur_shares_x", "is_sold_pur_shares_y"]].max(axis=1)

  c_df = c_df[[
               "Close_Price", 
               "Volume_non_block",
               "Today_High",
               "Today_Low",
               "no_days_not_traded_since_last_traded",
               "sentiment",
               "is_regarding_financial_report",
               "is_sold_pur_shares"]]

  # Save individually to file then to list for saving to single file
  c_df.to_csv("prices_sentiment_"+s+".csv")
  df_list.append(c_df)

# Combine then save all to file
dfs = pd.concat(df_list)
dfs.to_csv("prices_sentiment__all.csv")

/usr/local/lib/python3.7/dist-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  iloc._setitem_with_indexer(indexer, value)


In [20]:
dfs.corr()['Close_Price']

Close_Price                             1.000000
Volume_non_block                       -0.009635
Today_High                              0.999080
Today_Low                               0.999566
no_days_not_traded_since_last_traded    0.081076
sentiment                               0.013378
is_regarding_financial_report          -0.042616
is_sold_pur_shares                      0.004400
Name: Close_Price, dtype: float64

### Field: Determine if traded on previous business day

In [146]:
prices_df["is_traded_on_Previous_business_day"] = (ccc_df.Date.shift() == ccc_df.Previous_business_day )

In [147]:
prices_df

Symbol  ... is_traded_on_Previous_business_day
0               AFS  ...                                NaN
1               BRG  ...                                NaN
2               CCC  ...                              False
3               CAR  ...                                NaN
4                GK  ...                                NaN
...             ...  ...                                ...
63878  FIRSTROCKJMD  ...                                NaN
63879     CABROKERS  ...                                NaN
63880           TJH  ...                                NaN
63881        LUMBER  ...                                NaN
63882      TROPICAL  ...                                NaN

[63883 rows x 6 columns]

### Field: Calculate the previous day last traded

In [15]:
temp = ccc_df.Date.shift()
temp.iloc[0] = ccc_df.Date[ccc_df.Date.first_valid_index()]

In [16]:
ccc_df["Previous_trade_day"] = temp

### Calculate the number of days that the stock did not trade for prior to the current date

In [17]:
f = lambda x: (len(pd.bdate_range(x['Previous_trade_day'], x['Date'] )))

ccc_df['no_days_not_traded_since_last_traded'] = (ccc_df.apply(f, axis=1))

ccc_df['no_days_not_traded_since_last_traded'] = ccc_df['no_days_not_traded_since_last_traded'] -2
ccc_df.no_days_not_traded_since_last_traded.iloc[0] = 0 # Set the first date as zero as there is no data for it to check against

/usr/local/lib/python3.7/dist-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  iloc._setitem_with_indexer(indexer, value)


In [18]:
ccc_df[ccc_df.is_traded_on_Previous_business_day == False]

Symbol  ... no_days_not_traded_since_last_traded
2        CCC  ...                                    0
998      CCC  ...                                    1
2021     CCC  ...                                    3
3176     CCC  ...                                    1
3310     CCC  ...                                    2
...      ...  ...                                  ...
50668    CCC  ...                                    2
52749    CCC  ...                                    1
56412    CCC  ...                                    1
59986    CCC  ...                                    1
63571    CCC  ...                                    1

[68 rows x 7 columns]

## Determine the dates that the stock did not trade for

In [81]:
def getDatesToSumSentiments (x):
  date_list = list()
  for i in range(x['no_days_not_traded_since_last_traded']):
    date_list.append(
        x['Date'] - pd.tseries.offsets.BDay(i)
    )
  return date_list

In [82]:
ccc_df['stock_not_traded_date_list'] = ccc_df.apply(getDatesToSumSentiments, axis=1)

In [79]:
ccc_df

Symbol  ... stock_not_traded_date_list
2        CCC  ...                         []
30       CCC  ...                         []
69       CCC  ...                         []
105      CCC  ...                         []
143      CCC  ...                         []
...      ...  ...                        ...
63493    CCC  ...                         []
63571    CCC  ...      [2020-12-28 00:00:00]
63649    CCC  ...                         []
63732    CCC  ...                         []
63808    CCC  ...                         []

[1215 rows x 8 columns]

### Convert prices dataframe to 1NF by creating a separate row for each value in 'stock_not_traded_date_list'

In [94]:
ccc_df_exp = ccc_df.explode('stock_not_traded_date_list')

### Convert fields to string to faciliate join

In [128]:
ccc_df_exp.stock_not_traded_date_list = ccc_df_exp.stock_not_traded_date_list.dt.strftime("%Y-%m-%d")

In [127]:
sen_df.post_date = sen_df.post_date.dt.strftime("%Y-%m-%d")

### Perform join

In [129]:
ccc_com = pd.merge(  ccc_df_exp[["Symbol","Date","Close_Price","stock_not_traded_date_list"]],
                          ccc_sen_df[["post_date","sentiment","is_regarding_financial_report","is_sold_pur_shares"]], 
                          how='left',
                          left_on="stock_not_traded_date_list",right_on="post_date")

In [130]:
ccc_com

Symbol        Date  ...  is_regarding_financial_report is_sold_pur_shares
0       CCC  2016-01-04  ...                            NaN                NaN
1       CCC  2016-01-05  ...                            NaN                NaN
2       CCC  2016-01-06  ...                            NaN                NaN
3       CCC  2016-01-07  ...                            NaN                NaN
4       CCC  2016-01-08  ...                            NaN                NaN
...     ...         ...  ...                            ...                ...
1232    CCC  2020-12-24  ...                            NaN                NaN
1233    CCC  2020-12-28  ...                            NaN                NaN
1234    CCC  2020-12-29  ...                            NaN                NaN
1235    CCC  2020-12-30  ...                            NaN                NaN
1236    CCC  2020-12-31  ...                            NaN                NaN

[1237 rows x 8 columns]

## Combine price df and sentiment df

In [67]:
ccc_combined = pd.merge(  ccc_df[["Symbol","Date","Close_Price"]],
                          ccc_sen_df[["post_date","sentiment","is_regarding_financial_report","is_sold_pur_shares"]], 
                          how='left',
                          left_on="Date",right_on="post_date")


In [68]:
ccc_combined[~(ccc_combined.sentiment.isna())].drop(columns=["post_date"])

Symbol        Date  ...  is_regarding_financial_report  is_sold_pur_shares
16      CCC  2016-01-26  ...                            0.0                 0.0
36      CCC  2016-02-24  ...                            0.0                 0.0
39      CCC  2016-02-29  ...                            1.0                 0.0
42      CCC  2016-03-03  ...                            1.0                 0.0
63      CCC  2016-04-06  ...                            0.0                 0.0
...     ...         ...  ...                            ...                 ...
1110    CCC  2020-08-04  ...                            0.0                 0.0
1127    CCC  2020-08-28  ...                            0.0                 0.0
1168    CCC  2020-10-27  ...                            1.0                 0.0
1173    CCC  2020-11-03  ...                            0.0                 0.0
1193    CCC  2020-12-01  ...                            0.0                 0.0

[69 rows x 6 columns]